# Convert IEEE 14-Bus case from PandaPower to PGM via PGM IO

This notebook demonstrates the conversion of the IEEE 14-bus system from having PV generators to having all PQ nodes (except the slack bus).

## Conversion Process
1. Load the original IEEE 14-bus system using PandaPower.
2. The following modifications are made in PandaPower network:
    - vk_percent of all transformers are set to 10
    - Run PandaPower power flow, and then PV nodes are replaced with PQ nodes
3. Convert the PandaPower network to PGM format via PGM IO.
4. The following modifications are made in PGM network:
    - tan1 of some lines are set to 0 from NaN
5. Run PowerFlow in PGM to see if the conversion is successful.

## Result
- Original system: 1 slack bus + 4 PV generators + 9 PQ loads
- Converted system: 1 slack bus + 13 PQ loads

## Issue
1. Some lines have `tan1` as NaN after conversion of PGM-IO, which is not accepted by PGM. See [The Issue](#the-issue) section for details.

In [13]:
import pandas as pd
import numpy as np
import pandapower as pp
import pandapower.networks as pn
from power_grid_model_io.converters import PandaPowerConverter
import tempfile
from pathlib import Path
from power_grid_model.utils import json_serialize_to_file
from power_grid_model import (
    CalculationMethod,
    CalculationType,
    ComponentType,
    PowerGridModel,
)

# Convert

In [14]:
class PandaPowerNetwork2PGM:
    def __init__(
        self,
        net_name="ieee14",
        pv_to_pq=True,
        modify_vk_percent_in_pp=True,
        modify_tap_pos_in_pp=True,
        modify_tan1_in_pgm=True
    ):
        if net_name != "ieee14":
            raise ValueError("Currently only 'ieee14' network is supported.")
        self._load_pp_network()
        if modify_vk_percent_in_pp:
            self._modify_vk_percent_in_pp()
        if modify_tap_pos_in_pp:
            self._modify_tap_pos_in_pp()
        if pv_to_pq:
            self._replace_pv_nodes_with_pq_nodes()
        self._convert_to_pgm_format()
        if modify_tan1_in_pgm:
            self._modify_tan1_in_pgm()

    def _load_pp_network(self) -> None:
        """
        Load the IEEE 14-bus network from PandaPower
        """
        self.net = pn.case14()

    def _modify_tap_pos_in_pp(self) -> None:
        """
        modify the tap_pos of all transformers
        """
        tap_pos_before = self.net.trafo.loc[:, "tap_pos"].values.copy()
        tap_neutral_before = self.net.trafo.loc[:, "tap_neutral"].values.copy()
        # Apply modification
        for transformer in self.net.trafo.index:
            self.net.trafo.loc[transformer, "tap_pos"] = np.nan
            self.net.trafo.loc[transformer, "tap_neutral"] = np.nan
        tap_pos_after = self.net.trafo.loc[:, "tap_pos"].values.copy()
        tap_neutral_after = self.net.trafo.loc[:, "tap_neutral"].values.copy()
        # Create comparison table
        comparison_df = pd.DataFrame(
            {
                "Transformer": range(len(tap_pos_before)),
                "tap_pos Before": tap_pos_before,
                "tap_pos After": tap_pos_after,
                "tap_neutral Before": tap_neutral_before,
                "tap_neutral After": tap_neutral_after,
            }
        )
        self.tap_pos_comparison_df = comparison_df

    def _modify_vk_percent_in_pp(self) -> None:
        """
        modify the vk_percent of all transformers
        """
        # Get transformer data before modification
        vk_before = self.net.trafo.loc[:, "vk_percent"].values.copy()

        # Apply modification
        for transformer in self.net.trafo.index:
            self.net.trafo.loc[transformer, "vk_percent"] = 10

        # Get transformer data after modification
        vk_after = self.net.trafo.loc[:, "vk_percent"].values.copy()

        # Create comparison table
        comparison_df = pd.DataFrame(
            {
                "Transformer": range(len(vk_before)),
                "vk_percent Before": vk_before,
                "vk_percent After": vk_after,
            }
        )
        self.vk_percent_comparison_df = comparison_df

    def _replace_pv_nodes_with_pq_nodes(self) -> None:
        """
        Convert PV generators to PQ loads
        """

        # Get the current P and Q values from the generators
        gen_buses = self.net.gen.bus.values
        gen_p_mw = self.net.gen.p_mw.values
        # Run a power flow to get the actual Q values
        pp.runpp(self.net)
        print("------pandapower result------")
        print(pd.DataFrame(self.net.res_bus))
        gen_q_mvar = self.net.res_gen.q_mvar.values
        # replace the PV generators with PQ generators
        for i, bus in enumerate(gen_buses):
            pp.create_load(
                self.net,
                bus=bus,
                # the direction of power for load and generator is opposite
                p_mw=-gen_p_mw[i],
                q_mvar=-gen_q_mvar[i],
                name=f"static_load_{bus}",
            )
            print(
                f"Created load at bus {bus} with p_mw = {gen_p_mw[i]} and q_mvar = {gen_q_mvar[i]}")
        # Remove the original generators
        self.net.gen.drop(self.net.gen.index, inplace=True)

    def _convert_to_pgm_format(self) -> None:
        """
        Convert the network to PGM format
        """
        converter = PandaPowerConverter()
        self.input_data, self.extra_info = converter.load_input_data(self.net)

    def _modify_tan1_in_pgm(self) -> None:
        """
        modify the tan1 of all lines
        """
        tan1_before = self.input_data["line"]["tan1"].copy()

        for line in self.net.line.index:
            self.input_data["line"]["tan1"] = 0.0
        tan1_after = self.input_data["line"]["tan1"].copy()

        # Create comparison table
        comparison_df = pd.DataFrame(
            {
                "Line": range(len(tan1_before)),
                "tan1 Before": tan1_before,
                "tan1 After": tan1_after,
            }
        )
        self.tan1_comparison_df = comparison_df

In [15]:
ieee14_converter = PandaPowerNetwork2PGM(modify_vk_percent_in_pp=True, modify_tap_pos_in_pp=True,
                                         modify_tan1_in_pgm=True)

------pandapower result------
       vm_pu  va_degree        p_mw      q_mvar
0   1.060000   0.000000 -235.374733   40.011565
1   1.045000  -4.942948  -18.300000   39.781981
2   1.010000 -12.340770   94.200000   35.574963
3   1.087545 -11.240994   47.800000   -3.900000
4   1.070053  -9.489094    7.600000    1.600000
5   1.070000  -9.512059   11.200000    4.833509
6   1.088500 -11.247994    0.000000    0.000000
7   1.090000 -11.247994    0.000000 -161.877378
8   1.087954 -11.254991   29.500000   -5.889242
9   1.077380 -11.244354    9.000000    5.800000
10  1.070237 -10.539669    3.500000    1.800000
11  1.057702 -10.416046    6.100000    1.600000
12  1.054953 -10.600535   13.500000    5.800000
13  1.055875 -11.944374   14.900000    5.000000
Created load at bus 1 with p_mw = 40.0 and q_mvar = -27.081980660699305
Created load at bus 2 with p_mw = 0.0 and q_mvar = -16.57496337113983
Created load at bus 5 with p_mw = 0.0 and q_mvar = 2.6664905577888547
Created load at bus 7 with p_mw = 0.0 

/home/jhe/prjs/envs_py/uq4se-env/lib/python3.12/site-packages/power_grid_model_io/converters/pandapower_converter.py:426: RuntimeWarning: invalid value encountered in divide
  self._get_pp_attr("line", "g_us_per_km", expected_type="f8", default=0)
/home/jhe/prjs/envs_py/uq4se-env/lib/python3.12/site-packages/power_grid_model_io/converters/pandapower_converter.py:758: RuntimeWarning: invalid value encountered in divide
  rx_mag = mag_g / np.sqrt(i_no_load * i_no_load * 1e-4 - mag_g * mag_g)


For the first warning at line 426, 
```python
        pgm_lines["tan1"] = (
            self._get_pp_attr("line", "g_us_per_km", expected_type="f8", default=0)
            / c_nf_per_km
            / (2 * np.pi * self.system_frequency * 1e-3)
        )
```
from [pandapower_converter.py](https://github.com/PowerGridModel/power-grid-model-io/blob/main/src/power_grid_model_io/converters/pandapower_converter.py#L426)

Division by zero (`c_nf_per_km = 0`) happens here and the corresponding line has nan values for `tan1`. `c_nf_per_km` is line capacitance (line-to-earth) in nano Farad per km, with the valid range being >=0.

For the second warning at line 758, taking the square root of negative number happens here. Since i_no_load is zero, (i_no_load * i_no_load * 1e-4 - mag_g * mag_g) is negative. `i_no_load` is the relative no-load current, which corresponds to `i0` [in PGM](https://power-grid-model.readthedocs.io/en/stable/user_manual/components.html#id7). The relation between them is `i0 = i_no_load * rated_current` as seen in [pandapower_converter.py#L805](https://github.com/PowerGridModel/power-grid-model-io/blob/7b5d1aa4345aaeeb191d2705a7c231b546a15bcc/src/power_grid_model_io/converters/pandapower_converter.py#L805).
This is not really an issue now because manual zero sequence params are [not supported yet by PGM.](https://github.com/PowerGridModel/power-grid-model-io/blob/7b5d1aa4345aaeeb191d2705a7c231b546a15bcc/src/power_grid_model_io/converters/pandapower_converter.py#L749C47-L749C106)




In [16]:
input_data, extra_info = ieee14_converter.input_data, ieee14_converter.extra_info

# Check the Modifications
Motivations for the modifications are stated in the following sections.

In [17]:
# print the comparison tables
print(' --- Modifications in PandaPower ---')
print(ieee14_converter.vk_percent_comparison_df)
print(ieee14_converter.tap_pos_comparison_df)

 --- Modifications in PandaPower ---
   Transformer  vk_percent Before  vk_percent After
0            0           2070.288              10.0
1            1           5506.182              10.0
2            2           2494.998              10.0
3            3           1743.885              10.0
4            4           1089.099              10.0
   Transformer  tap_pos Before  tap_pos After  tap_neutral Before  \
0            0            -1.0            NaN                 0.0   
1            1            -1.0            NaN                 0.0   
2            2            -1.0            NaN                 0.0   
3            3             NaN            NaN                 NaN   
4            4             NaN            NaN                 NaN   

   tap_neutral After  
0                NaN  
1                NaN  
2                NaN  
3                NaN  
4                NaN  


`vk_percent` is the relative short-circuit voltage in percent, which should equal `uk` * 100 in PGM. Therefore, the theoretical range of `vk_percent` should be `[0, 100]`, according to PGM's [documentation](https://power-grid-model.readthedocs.io/en/stable/user_manual/components.html#transformer). [It is also known](https://elektro.fs.cvut.cz/en/SSem/e141503.pdf/Transformers) that `vk_percent` usually ranges from 2 to 10 %. 
Since the original `vk_percent`s in PandaPower network are above 100, even above 1000, all the `vk_percent`s are modified to 10.

`tap_pos` is the tap position of the transformer, which should be an integer between `tap_min` and `tap_max`. However, in the original PandaPower network, `tap_min` and `tap_max` are not set for any transformer. Therefore, all the `tap_pos` and `tap_neutral` are set to NaN. `tap_neutral` is the tap position where the transformer ratio is equal to the ratio of the rated voltages.

In [18]:
# print tap_min, tap_max, tap_neutral of all transformers
print(' --- tap_min, tap_max of all transformers ---')
print(ieee14_converter.net.trafo[['tap_min', 'tap_max']])

 --- tap_min, tap_max of all transformers ---
   tap_min  tap_max
0      NaN      NaN
1      NaN      NaN
2      NaN      NaN
3      NaN      NaN
4      NaN      NaN


# The Issue

<div style="background-color: #ffcccc; padding: 10px; border-left: 4px solid #ff0000; color: #cc0000;">
<strong>⚠️ Issue:</strong> When there is no line capacitance, e.g. `c_nf_per_km = 0`, PGM-IO sets `tan1` to NaN. Instead, it should be set to 0 to match the fact that there is no shunt admittance.
</div>

In [19]:
print(' --- Modifications in PGM ---')
print(ieee14_converter.tan1_comparison_df)

 --- Modifications in PGM ---
    Line  tan1 Before  tan1 After
0      0          0.0         0.0
1      1          0.0         0.0
2      2          0.0         0.0
3      3          0.0         0.0
4      4          0.0         0.0
5      5          0.0         0.0
6      6          NaN         0.0
7      7          NaN         0.0
8      8          NaN         0.0
9      9          NaN         0.0
10    10          NaN         0.0
11    11          NaN         0.0
12    12          NaN         0.0
13    13          NaN         0.0
14    14          NaN         0.0


`tan1` is the [positive-sequence shunt loss factor](https://power-grid-model.readthedocs.io/en/stable/user_manual/components.html#id5), or tangent of the shunt impedance angle. Since some of the lines in PandaPower network have zero `c_nf_per_km` (line capacitance), `tan1` is then set to NaN in PGM-IO. However, PGM does not accept NaN values for `tan1`, so all the `tan1`s are set to 0, which matches the fact that there is no shunt admittance from the lines.

# Run Power Flow in PandaPower

In [20]:
pp_net = ieee14_converter.net
# set vk_percent to 10
pp_net.trafo.loc[:, "vk_percent"] = 10
runpp = pp.runpp(pp_net, calculate_voltage_angles=True)
print("------pandapower result------")
print(pd.DataFrame(pp_net.res_bus))

------pandapower result------
       vm_pu  va_degree        p_mw      q_mvar
0   1.060000   0.000000 -235.374733   40.011565
1   1.045000  -4.942948  -18.300000   39.781981
2   1.010000 -12.340770   94.200000   35.574963
3   1.087545 -11.240994   47.800000   -3.900000
4   1.070053  -9.489094    7.600000    1.600000
5   1.070000  -9.512059   11.200000    4.833509
6   1.088500 -11.247994    0.000000    0.000000
7   1.090000 -11.247994    0.000000 -161.877378
8   1.087954 -11.254991   29.500000   -5.889242
9   1.077380 -11.244354    9.000000    5.800000
10  1.070237 -10.539669    3.500000    1.800000
11  1.057702 -10.416046    6.100000    1.600000
12  1.054953 -10.600535   13.500000    5.800000
13  1.055875 -11.944374   14.900000    5.000000


# Run Power Flow in PGM

In [21]:
from power_grid_model.validation import assert_valid_input_data

assert_valid_input_data(
    input_data, calculation_type=CalculationType.power_flow, symmetric=True
)

In [22]:
model = PowerGridModel(input_data)

In [23]:
output_data = model.calculate_power_flow(
    symmetric=True,
    error_tolerance=1e-8,
    max_iterations=20,
    calculation_method=CalculationMethod.newton_raphson,
)

# result dataset
print("------node result------")
print(pd.DataFrame(output_data[ComponentType.node]))

------node result------
    id  energized      u_pu              u   u_angle             p  \
0    0          1  1.060926  143224.962486 -0.021141  2.353278e+08   
1    1          1  1.044589  141019.557445 -0.106952  1.830000e+07   
2    2          1  1.008827  136191.619228 -0.236070 -9.420000e+07   
3    3          1  1.086656  146698.599056 -0.216878 -4.780000e+07   
4    4          1  1.069258  144349.769845 -0.186286 -7.600000e+06   
5    5          1  1.069204     222.394485 -0.186688 -1.120000e+07   
6    6          1  1.087611   15226.560703 -0.217000 -8.640581e-06   
7    7          1  1.089113   13069.353786 -0.217000 -2.202682e-06   
8    8          1  1.087065     226.109592 -0.217123 -2.950000e+07   
9    9          1  1.076501     223.912297 -0.216941 -9.000000e+06   
10  10          1  1.069397     222.434529 -0.204635 -3.500000e+06   
11  11          1  1.056888     219.832774 -0.202488 -6.100000e+06   
12  12          1  1.054130     219.259002 -0.205709 -1.350000e+07

# Save the grid in PGM format

In [24]:
# save the grid to a json file
temp_path = Path(tempfile.gettempdir())
json_serialize_to_file(Path("ieee14_in_pgm.json"), input_data)